<a href="https://colab.research.google.com/github/graylan0/quantum-machine-learning/blob/main/backup.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install --pre torch torchvision -f https://download.pytorch.org/whl/nightly/cu102/torch_nightly.html -U
!pip install git+https://github.com/suno-ai/bark.git
!pip install openai
!pip install scipy

Looking in links: https://download.pytorch.org/whl/nightly/cu102/torch_nightly.html
  Cloning https://github.com/suno-ai/bark.git to /tmp/pip-req-build-llex05fq
  Running command git clone --filter=blob:none --quiet https://github.com/suno-ai/bark.git /tmp/pip-req-build-llex05fq
  Resolved https://github.com/suno-ai/bark.git to commit 42d579ddcd2089be7791ba65f22abd99e0ce63a5
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 135.8/135.8 kB 2.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.7/3.7 MB 16.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 294.8/294.8 kB 19.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.8/3.8 MB 37.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.6/7.6 MB 62.5 MB/s eta 0:00:00
    

In [2]:
!pip install scipy
!pip install sounddevice
!pip install fastapi uvicorn

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 66.2/66.2 kB 1.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.5/59.5 kB 4.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 67.0/67.0 kB 7.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.6 MB/s eta 0:00:00


In [4]:
from bark import SAMPLE_RATE, generate_audio, preload_models
from scipy.io.wavfile import write as write_wav
from IPython.display import Audio
from concurrent.futures import ThreadPoolExecutor
import numpy as np
import uuid
import os

# Preload models
preload_models()

os.environ["SUNO_USE_SMALL_MODELS"] = "True"

def generate_audio_for_sentence(sentence):
    return generate_audio(sentence)

def generate_response(song_elements, num_threads=4):
    pieces = []

    with ThreadPoolExecutor(max_workers=num_threads) as executor:
        future_to_element = {executor.submit(generate_audio_for_sentence, element.get('lyrics', element.get('music'))): element for element in song_elements if 'lyrics' in element or 'music' in element}

        for future in future_to_element:
            audio_array = future.result()
            pieces += [audio_array]

            element = future_to_element[future]
            if 'pause' in element:
                silence = np.zeros(int(element['pause'] * SAMPLE_RATE))
                pieces += [silence]

    audio = np.concatenate(pieces)
    file_name = str(uuid.uuid4()) + ".wav"
    write_wav(file_name, SAMPLE_RATE, audio.astype(np.int16))
    print(f"Audio generation completed and saved to {file_name}")
    return Audio(audio, rate=SAMPLE_RATE)

song_elements = [
    {'music': "[music]Soft ukulele strums, [music]tempo 120", '[music]pause': 2},
    {'lyrics': "[music]Love on the island, sun in the sky, feeling so high", '[music]pause': 1},
    {'lyrics': "[music]The breeze whispers secrets, as we let the time fly", '[music]pause': 2},
    {'lyrics': "[music]Dance, dance, under the moonlight, let's make this a beautiful night", '[music]pause': 1},
    {'music': "[music]music", '[music]pause': 1},
    {'lyrics': "[music]Waves are crashing, hearts are smashing, yet we're so free", '[music]pause': 2},
    {'lyrics': "[music]The stars are our spotlight, as we carve our love on a palm tree", '[music]pause': 1},
    {'music': "[music]music", '[music]pause': 1},
    {'lyrics': "[music]But we're still here, love's so clear, like the ocean so deep", '[music]pause': 2},
    {'lyrics': "[music]Dance, dance, under the moonlight, let's make memories to keep", '[music]pause': 1},
    {'lyrics': "[music]And so we say Aloha, as the sun greets the dawn", '[music]pause': 2},
    {'end': "[music]Soft ukulele fade-out, [music]tempo slows to 90"}
]

audio_output = generate_response(song_elements)
audio_output  # This should play the audio in the notebook



  0%|          | 0/768 [00:00<?, ?it/s]

  0%|          | 0/768 [00:00<?, ?it/s]


  0%|          | 0/768 [00:00<?, ?it/s]


  0%|          | 1/768 [00:00<07:13,  1.77it/s]

  0%|          | 1/768 [00:00<07:21,  1.74it/s]


  0%|          | 3/768 [00:00<02:32,  5.03it/s]

  0%|          | 3/768 [00:00<02:41,  4.74it/s]


  1%|          | 5/768 [00:00<01:41,  7.49it/s]


  1%|          | 6/768 [00:00<01:16,  9.90it/s]

  1%|          | 5/768 [00:00<01:59,  6.36it/s]


  1%|          | 7/768 [00:01<01:35,  7.97it/s]

  1%|          | 7/768 [00:01<01:36,  7.87it/s]


  1%|          | 9/768 [00:01<01:23,  9.07it/s]

  1%|          | 9/768 [00:01<01:26,  8.80it/s]


  1%|▏         | 11/768 [00:01<01:17,  9.83it/s]


  2%|▏         | 14/768 [00:01<00:56, 13.40it/s]

  2%|▏         | 13/768 [00:01<01:07, 11.26it/s]


  2%|▏         | 16/768 [00:01<00:56, 13.33it/s]

  2%|▏         | 15/768 [00:01<01:03, 11.80it/s]

  2%|▏         | 15/768 [00:01<01:02, 12.14it/s]


  2%|▏         | 17/768 [00

Audio generation completed and saved to b493e558-5048-4bb7-8044-2516c1eb8bd5.wav
